In [22]:
# MLP for Pima Indians Dataset Serialize to JSON and HDF5
import numpy as np
import os
import cv2
from collections import deque
import pafy
import math
import random
import datetime as dt
import tensorflow as tf
import matplotlib.pyplot as plt
import keras
from moviepy.editor import *
%matplotlib inline
 
from sklearn.model_selection import train_test_split
 
from tensorflow.keras.layers import *
from tensorflow.keras.models import Sequential
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.callbacks import EarlyStopping
from tensorflow.keras.utils import plot_model

In [29]:
SEQUENCE_LENGTH = 40
IMAGE_HEIGHT , IMAGE_WIDTH = 64, 64
CLASSES_LIST = ["normal", "nude", "Violence"]

In [24]:
# load json and create model
json_file = open('LRCN_model.json', 'r')
loaded_model_json = json_file.read()
json_file.close()
LRCN_model = model_from_json(loaded_model_json)
# load weights into new model
LRCN_model.load_weights("LRCN_model.h5")
print("Loaded model from disk")

Loaded model from disk


In [90]:
!pip3 install pytube==6.4.2

Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com


In [93]:
# importing the module 
from pytube import YouTube 
  
# where to save 
SAVE_PATH = "test_videos_1" #to_do 
  
# link of the video to be downloaded 
link="https://www.youtube.com/watch?v=xWOoBJUqlbI"
yt = YouTube(link)
stream = yt.streams.first()
out_file = stream.download(SAVE_PATH)
print(out_file)
os.rename(outfile, )

'/home/subham/Desktop/upwork/project30/obscene-video-recognition/approach2/test_videos_1/Search in an almost sorted array  GeeksforGeeks.3gpp'

In [85]:
# Make the Output directory if it does not exist
test_videos_directory = 'test_videos_1'
os.makedirs(test_videos_directory, exist_ok = True)
video_title='TestVideo'
# Download a YouTube Video.
yt_download("",test_videos_directory+'/'+video_title+'.mp4')

# Get the YouTube Video's path we just downloaded.
input_video_file_path = f'{test_videos_directory}/{video_title}.mp4'

download https://www.youtube.com/shorts/pnPkjqX6XAA in format mp4 to file test_videos_1/TestVideo.mp4
[generic] pnPkjqX6XAA: Requesting header


[generic] pnPkjqX6XAA: Downloading webpage
[generic] pnPkjqX6XAA: Extracting information
[youtube] pnPkjqX6XAA: Downloading webpage
[download] Destination: test_videos_1/TestVideo.mp4
[download] 100% of 3.96MiB in 00:5331KiB/s ETA 00:008nown ETA
Done downloading, now converting ...


In [86]:
def predict_on_video(video_file_path, output_file_path, SEQUENCE_LENGTH):
    '''# Construct the output video path.
output_video_file_path = f'{test_videos_directory}/{video_title}-Output-SeqLen{SEQUENCE_LENGTH}.mp4'
 
# Perform Action Recognition on the Test Video.
predict_on_video(input_video_file_path, output_video_file_path, SEQUENCE_LENGTH)
 
# Display the output video.
VideoFileClip(output_video_file_path, audio=False, target_resolution=(300,None)).ipython_display()
    This function will perform action recognition on a video using the LRCN model.
    Args:
    video_file_path:  The path of the video stored in the disk on which the action recognition is to be performed.
    output_file_path: The path where the ouput video with the predicted action being performed overlayed will be stored.
    SEQUENCE_LENGTH:  The fixed number of frames of a video that can be passed to the model as one sequence.
    '''
 
    # Initialize the VideoCapture object to read from the video file.
    video_reader = cv2.VideoCapture(video_file_path)
 
    # Get the width and height of the video.
    original_video_width = int(video_reader.get(cv2.CAP_PROP_FRAME_WIDTH))
    original_video_height = int(video_reader.get(cv2.CAP_PROP_FRAME_HEIGHT))
 
    # Initialize the VideoWriter Object to store the output video in the disk.
    video_writer = cv2.VideoWriter(output_file_path, cv2.VideoWriter_fourcc('M', 'P', '4', 'V'), 
                                   video_reader.get(cv2.CAP_PROP_FPS), (original_video_width, original_video_height))
    print(output_file_path)
    # Declare a queue to store video frames.
    frames_queue = deque(maxlen = SEQUENCE_LENGTH)
 
    # Initialize a variable to store the predicted action being performed in the video.
    predicted_class_name = ''
 
    # Iterate until the video is accessed successfully.
    while video_reader.isOpened():
 
        # Read the frame.
        ok, frame = video_reader.read() 
        
        # Check if frame is not read properly then break the loop.
        if not ok:
            break
 
        # Resize the Frame to fixed Dimensions.
        resized_frame = cv2.resize(frame, (IMAGE_HEIGHT, IMAGE_WIDTH))
        
        # Normalize the resized frame by dividing it with 255 so that each pixel value then lies between 0 and 1.
        normalized_frame = resized_frame / 255
 
        # Appending the pre-processed frame into the frames list.
        frames_queue.append(normalized_frame)
 
        # Check if the number of frames in the queue are equal to the fixed sequence length.
        if len(frames_queue) == SEQUENCE_LENGTH:
 
            # Pass the normalized frames to the model and get the predicted probabilities.
            predicted_labels_probabilities = LRCN_model.predict(np.expand_dims(frames_queue, axis = 0))[0]
 
            # Get the index of class with highest probability.
            predicted_label = np.argmax(predicted_labels_probabilities)
            
            # Get the class name using the retrieved index.
            predicted_class_name = CLASSES_LIST[predicted_label]
            print(predicted_labels_probabilities, predicted_class_name) 
        # Write predicted class name on top of the frame.
        cv2.putText(frame, predicted_class_name, (10, 30), cv2.FONT_HERSHEY_SIMPLEX, 1, (0, 255, 0), 2)
 
        # Write The frame into the disk using the VideoWriter Object.
        video_writer.write(frame)
        
    # Release the VideoCapture and VideoWriter objects.
    video_reader.release()
    video_writer.release()

In [87]:
# Construct the output video path.
output_video_file_path = f'{test_videos_directory}/{video_title}-Output-SeqLen{SEQUENCE_LENGTH}.mp4'
 
# Perform Action Recognition on the Test Video.
predict_on_video(input_video_file_path, output_video_file_path, SEQUENCE_LENGTH)
 
# Display the output video.
VideoFileClip(output_video_file_path, audio=False, target_resolution=(300,None)).ipython_display()

test_videos_1/TestVideo-Output-SeqLen40.mp4
1/1 [==============================] - 0s 14ms/step
[0.01852975 0.00188157 0.9795887 ] Violence
1/1 [==============================] - 0s 14ms/step
[0.01463945 0.00170121 0.98365927] Violence
1/1 [==============================] - 0s 14ms/step
[0.012348   0.00160233 0.9860497 ] Violence


OpenCV: FFMPEG: tag 0x5634504d/'MP4V' is not supported with codec id 12 and format 'mp4 / MP4 (MPEG-4 Part 14)'
OpenCV: FFMPEG: fallback to use tag 0x7634706d/'mp4v'


1/1 [==============================] - 0s 14ms/step
[0.01058071 0.0014874  0.9879319 ] Violence
1/1 [==============================] - 0s 14ms/step
[0.00914984 0.00138862 0.9894615 ] Violence
1/1 [==============================] - 0s 14ms/step
[0.0083494  0.00137922 0.9902714 ] Violence
1/1 [==============================] - 0s 14ms/step
[0.00774635 0.00138146 0.9908722 ] Violence
1/1 [==============================] - 0s 14ms/step
[0.0075298  0.0014115  0.99105865] Violence
1/1 [==============================] - 0s 14ms/step
[0.00773954 0.00146    0.99080044] Violence
1/1 [==============================] - 0s 14ms/step
[0.00805192 0.00154519 0.99040294] Violence
1/1 [==============================] - 0s 14ms/step
[0.00872272 0.00171993 0.9895573 ] Violence
1/1 [==============================] - 0s 14ms/step
[0.00925418 0.00184799 0.98889786] Violence
1/1 [==============================] - 0s 14ms/step
[0.00923857 0.00186019 0.98890126] Violence
1/1 [==============================] - 0

1/1 [==============================] - 0s 12ms/step
[0.0053284  0.00100852 0.9936631 ] Violence
1/1 [==============================] - 0s 11ms/step
[5.1140664e-03 9.8106114e-04 9.9390489e-01] Violence
1/1 [==============================] - 0s 11ms/step
[4.8043090e-03 9.2654239e-04 9.9426913e-01] Violence
1/1 [==============================] - 0s 11ms/step
[4.5709503e-03 9.0173422e-04 9.9452728e-01] Violence
1/1 [==============================] - 0s 12ms/step
[0.0049038  0.00100469 0.99409145] Violence
1/1 [==============================] - 0s 12ms/step
[0.00506185 0.00105819 0.9938799 ] Violence
1/1 [==============================] - 0s 12ms/step
[0.0050081 0.0010705 0.9939214] Violence
1/1 [==============================] - 0s 11ms/step
[0.005075   0.00108663 0.99383837] Violence
1/1 [==============================] - 0s 11ms/step
[0.00489291 0.00104325 0.9940639 ] Violence
1/1 [==============================] - 0s 12ms/step
[0.00488443 0.00105983 0.99405575] Violence
1/1 [===========

1/1 [==============================] - 0s 11ms/step
[4.0982915e-03 9.2472008e-04 9.9497694e-01] Violence
1/1 [==============================] - 0s 11ms/step
[3.7872265e-03 8.5729215e-04 9.9535549e-01] Violence
1/1 [==============================] - 0s 11ms/step
[3.7266405e-03 8.4742188e-04 9.9542600e-01] Violence
1/1 [==============================] - 0s 11ms/step
[3.725188e-03 8.423684e-04 9.954325e-01] Violence
1/1 [==============================] - 0s 11ms/step
[3.5578157e-03 8.0439384e-04 9.9563783e-01] Violence
1/1 [==============================] - 0s 11ms/step
[3.496303e-03 8.119982e-04 9.956917e-01] Violence
1/1 [==============================] - 0s 10ms/step
[3.5962395e-03 8.5023843e-04 9.9555355e-01] Violence
1/1 [==============================] - 0s 11ms/step
[3.5720025e-03 8.3727075e-04 9.9559081e-01] Violence
1/1 [==============================] - 0s 11ms/step
[3.5769474e-03 8.3938183e-04 9.9558371e-01] Violence
1/1 [==============================] - 0s 11ms/step
[3.713637

...

1/1 [==============================] - 0s 11ms/step
[0.01254584 0.00163291 0.9858212 ] Violence
1/1 [==============================] - 0s 11ms/step
[0.01229554 0.00164801 0.98605645] Violence
1/1 [==============================] - 0s 11ms/step
[0.01319101 0.00164409 0.9851649 ] Violence
1/1 [==============================] - 0s 11ms/step
[0.01452775 0.00165209 0.9838202 ] Violence
1/1 [==============================] - 0s 11ms/step
[0.01486188 0.00170266 0.98343545] Violence
1/1 [==============================] - 0s 11ms/step
[0.01611723 0.00180301 0.98207974] Violence
1/1 [==============================] - 0s 11ms/step
[0.01839035 0.00201259 0.97959703] Violence
1/1 [==============================] - 0s 11ms/step
[0.02178358 0.00226121 0.9759552 ] Violence
1/1 [==============================] - 0s 11ms/step
[0.0246049  0.00244089 0.9729542 ] Violence
1/1 [==============================] - 0s 11ms/step
[0.02833281 0.002634   0.9690332 ] Violence
1/1 [==============================] - 0

1/1 [==============================] - 0s 11ms/step
[0.00552363 0.00105762 0.99341875] Violence
1/1 [==============================] - 0s 11ms/step
[0.00638658 0.00120298 0.9924104 ] Violence
1/1 [==============================] - 0s 11ms/step
[0.0079546  0.00143515 0.9906102 ] Violence
1/1 [==============================] - 0s 11ms/step
[0.00913044 0.00162413 0.9892454 ] Violence
1/1 [==============================] - 0s 11ms/step
[0.0099099  0.00176319 0.98832697] Violence
1/1 [==============================] - 0s 11ms/step
[0.01058013 0.00189556 0.9875243 ] Violence
1/1 [==============================] - 0s 11ms/step
[0.01051173 0.00177101 0.98771733] Violence
1/1 [==============================] - 0s 12ms/step
[0.01067937 0.00166549 0.9876552 ] Violence
1/1 [==============================] - 0s 11ms/step
[0.01191135 0.00173119 0.98635745] Violence
1/1 [==============================] - 0s 11ms/step
[0.014975   0.0020052  0.98301977] Violence
1/1 [==============================] - 0

1/1 [==============================] - 0s 12ms/step
[0.01241891 0.00239371 0.98518735] Violence
1/1 [==============================] - 0s 11ms/step
[0.00994898 0.00173795 0.98831314] Violence
1/1 [==============================] - 0s 11ms/step
[0.00724137 0.00113737 0.99162126] Violence
1/1 [==============================] - 0s 11ms/step
[5.5201063e-03 8.2758290e-04 9.9365234e-01] Violence
1/1 [==============================] - 0s 11ms/step
[4.6858508e-03 6.8837550e-04 9.9462575e-01] Violence
1/1 [==============================] - 0s 11ms/step
[4.2659137e-03 6.5141032e-04 9.9508274e-01] Violence
1/1 [==============================] - 0s 10ms/step
[4.3898304e-03 6.9621217e-04 9.9491394e-01] Violence
1/1 [==============================] - 0s 11ms/step
[4.5653046e-03 7.5035216e-04 9.9468440e-01] Violence
1/1 [==============================] - 0s 11ms/step
[5.0275787e-03 8.5268397e-04 9.9411976e-01] Violence
1/1 [==============================] - 0s 11ms/step
[5.1513775e-03 8.5514557e-04 9

1/1 [==============================] - 0s 11ms/step
[4.315448e-02 5.671040e-04 9.562784e-01] Violence
1/1 [==============================] - 0s 11ms/step
[5.517545e-02 6.024929e-04 9.442221e-01] Violence
1/1 [==============================] - 0s 11ms/step
[6.8922788e-02 6.4036075e-04 9.3043679e-01] Violence
1/1 [==============================] - 0s 12ms/step
[8.421672e-02 6.785965e-04 9.151047e-01] Violence
1/1 [==============================] - 0s 11ms/step
[1.00913644e-01 7.18384224e-04 8.98368001e-01] Violence
1/1 [==============================] - 0s 12ms/step
[1.1875668e-01 7.5680774e-04 8.8048649e-01] Violence
1/1 [==============================] - 0s 12ms/step
[1.3743035e-01 7.9421699e-04 8.6177540e-01] Violence
1/1 [==============================] - 0s 12ms/step
[1.5687048e-01 8.3116628e-04 8.4229833e-01] Violence
1/1 [==============================] - 0s 11ms/step
[0.17664912 0.00086534 0.8224855 ] Violence
1/1 [==============================] - 0s 11ms/step
[0.19650511 0.0008

Moviepy - Done !
Moviepy - video ready __temp__.mp4
